In [42]:
%%HTML
<script>
    code_show=true; 
    function code_toggle() {
        if (code_show) { $('div.input').hide(); }
        else { $('div.input').show(); }
        code_show = !code_show
    } 
$( document ).ready(code_toggle);
</script>

<form action="javascript:code_toggle()">
    <b><input type="submit" value="单击此处切换代码显示"></b>
</form>

# 一次性剔除数据的趋势项 

## 原始数据
时长500秒

In [43]:
from os import listdir, path

folder = 'tdms_files'
file_list = [path.join(folder, file_name) for file_name in listdir(folder)][0:50]

In [44]:
from read_tdms_file import read_tdms_files

channel_list = [u'NLHQ-X-03-S08', u'NLHQ-X-03-S09']
raw_data = read_tdms_files(file_list, channel_list)

In [45]:
import pandas as pd

pd.options.display.max_rows = 20
raw_data

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:00.000     219.117111    -828.362610
2018-03-11 10:00:00.020     219.414963    -828.970520
2018-03-11 10:00:00.040     219.210724    -828.194641
2018-03-11 10:00:00.060     218.844788    -828.614563
2018-03-11 10:00:00.080     218.921371    -827.882690
2018-03-11 10:00:00.100     218.129944    -827.966675
2018-03-11 10:00:00.120     218.942657    -828.466614
2018-03-11 10:00:00.140     218.972443    -827.926636
2018-03-11 10:00:00.160     218.712875    -828.346619
2018-03-11 10:00:00.180     219.397934    -828.506592
...                                ...            ...
2018-03-11 10:04:09.800     232.699158    -818.855835
2018-03-11 10:04:09.820     232.975723    -818.571899
2018-03-11 10:04:09.840     233.086365    -818.807861
2018-03-11 10:04:09.860     231.775818    -820.463623
2018-03-11 10:04:09.880     230.988632    -820.823608
2018-03-11 10:04:09.900     231.971542    -820.939575
2018-03-11 10:04:09.920     231.294998    -820.955566
2018-03-11 10:04:09.940     231.682205    -820.999573
2018-03-11 10:04:09.960     231.682205    -821.015564
2018-03-11 10:04:09.980     231.933243    -820.507629

[12500 rows x 2 columns]

In [46]:
# 定义绘制Pandas DataFrame曲线的函数
from pyecharts import Line

def dataframe_line_plot(title, df):
    
    option = {
        'title': {
            'text': title,
            'left': 'center'
        },
        'legend': {
            'show': True,
            'orient': 'vertical',
            'right': '9%',
            'top': '3%'
        },
        'xAxis': {
            'type': 'time',
            'axisLine': {
                'onZero': False
            }
        },
        'yAxis': {
            'axisLine': {
                'onZero': False
            }
        },
        'dataZoom': [
            {
                'type': 'slider',
                'xAxisIndex': 0,
                'start': 0,
                'end': 50
            }
        ]
    }

    time = [ts.timestamp()/0.001 for ts in df.index]
    series = []
    for channel in df.columns:
        values = df[channel].values.tolist()
        data = [(t, x) for t, x in zip(time, values)]
        series.append(
            {
                'type': 'line',
                'showSymbol': False,
                'name': channel,
                'data': data
            }
        )
    option.update({'series': series})
        
    line_plot = Line()
    line_plot._option.update(option)
    return line_plot

In [47]:
line_plot = dataframe_line_plot('原始数据绘图', raw_data)
line_plot

## 减采样（周期=5秒）并计算新周期内的众数
固定时间区间内的众数较好地反映了趋势项，但是时间区间的宽度必须合适，区间太宽不能认为该区间中趋势保持不变，区间太窄可能导致众数不能代表趋势。

In [48]:
from scipy.stats import mode

mode_5s = raw_data.resample('5s', closed='right', label='right').apply(lambda x: mode(x)[0][0])

In [49]:
mode_5s

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:00     219.117111    -828.362610
2018-03-11 10:00:05     218.989456    -828.602539
2018-03-11 10:00:10     218.525665    -828.254639
2018-03-11 10:00:15     219.163910    -827.570679
2018-03-11 10:00:20     218.538422    -829.802429
2018-03-11 10:00:25     218.861801    -827.746704
2018-03-11 10:00:30     219.210724    -828.586548
2018-03-11 10:00:35     219.636215    -828.614563
2018-03-11 10:00:40     219.146896    -828.482605
2018-03-11 10:00:45     218.878830    -828.894531
...                            ...            ...
2018-03-11 10:03:25     228.027130    -823.315247
2018-03-11 10:03:30     228.958984    -823.507263
2018-03-11 10:03:35     228.831329    -822.083435
2018-03-11 10:03:40     229.584473    -823.283264
2018-03-11 10:03:45     229.878067    -823.135315
2018-03-11 10:03:50     229.971680    -823.359253
2018-03-11 10:03:55     230.256760    -821.451538
2018-03-11 10:04:00     230.652481    -820.911560
2018-03-11 10:04:05     231.363068    -821.107544
2018-03-11 10:04:10     231.711990    -820.463623

[51 rows x 2 columns]

In [50]:
line_plot = dataframe_line_plot('5秒内众数绘图', mode_5s)
line_plot

## 计算5秒众数的滑动平均值
为进一步平滑趋势项，将每个区间及其左右相邻区间的众数的平均值作为该区间的趋势项。

In [51]:
mode_5s = mode_5s.rolling(3, center=True, min_periods=1).mean()

In [52]:
mode_5s

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:00     219.053284    -828.482574
2018-03-11 10:00:05     218.877411    -828.406596
2018-03-11 10:00:10     218.893010    -828.142619
2018-03-11 10:00:15     218.742666    -828.542582
2018-03-11 10:00:20     218.854711    -828.373271
2018-03-11 10:00:25     218.870316    -828.711894
2018-03-11 10:00:30     219.236247    -828.315938
2018-03-11 10:00:35     219.331278    -828.561239
2018-03-11 10:00:40     219.220647    -828.663900
2018-03-11 10:00:45     218.962509    -828.822550
...                            ...            ...
2018-03-11 10:03:25     228.156199    -823.399251
2018-03-11 10:03:30     228.605815    -822.968648
2018-03-11 10:03:35     229.124929    -822.957987
2018-03-11 10:03:40     229.431290    -822.834005
2018-03-11 10:03:45     229.811406    -823.259277
2018-03-11 10:03:50     230.035502    -822.648702
2018-03-11 10:03:55     230.293640    -821.907450
2018-03-11 10:04:00     230.757436    -821.156881
2018-03-11 10:04:05     231.242513    -820.827576
2018-03-11 10:04:10     231.537529    -820.785583

[51 rows x 2 columns]

In [53]:
line_plot = dataframe_line_plot('众数滑动平均值绘图', mode_5s)
line_plot

## 提出趋势项后的数据
首先对上一步获取的趋势项增采样（周期=0.02秒），然后删除最后一项以保证趋势项数据与原数据长度相同。

In [54]:
trend = mode_5s.resample('20ms').interpolate()
trend = trend[:-1]
detrended_data = raw_data - trend

In [55]:
line_plot = dataframe_line_plot('剔除趋势项的数据绘图', detrended_data)
line_plot

# 剔除乱序到来数据包的趋势项

## 3个原始数据包
**注意**：最后一个数据包最先到达

In [56]:
from read_tdms_file import read_tdms_file

df1 = read_tdms_file(file_list[2], channel_list=channel_list)
df2 = read_tdms_file(file_list[0], channel_list=channel_list)
df3 = read_tdms_file(file_list[1], channel_list=channel_list)

In [57]:
df1

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:10.000     219.712814    -827.826660
2018-03-11 10:00:10.020     219.427719    -827.842651
2018-03-11 10:00:10.040     219.036255    -827.706665
2018-03-11 10:00:10.060     219.334106    -828.246643
2018-03-11 10:00:10.080     219.466019    -828.510559
2018-03-11 10:00:10.100     219.810669    -828.986511
2018-03-11 10:00:10.120     218.768188    -829.130493
2018-03-11 10:00:10.140     218.955414    -828.614563
2018-03-11 10:00:10.160     218.751175    -828.898499
2018-03-11 10:00:10.180     219.763870    -827.890686
...                                ...            ...
2018-03-11 10:00:14.800     218.780960    -828.986511
2018-03-11 10:00:14.820     217.853363    -831.098267
2018-03-11 10:00:14.840     217.823578    -830.822266
2018-03-11 10:00:14.860     218.780960    -829.834412
2018-03-11 10:00:14.880     219.083069    -828.018616
2018-03-11 10:00:14.900     219.572388    -826.294861
2018-03-11 10:00:14.920     220.419144    -826.074890
2018-03-11 10:00:14.940     220.461700    -826.234863
2018-03-11 10:00:14.960     219.648987    -826.346863
2018-03-11 10:00:14.980     220.525528    -826.898804

[250 rows x 2 columns]

In [58]:
df2

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:00.000     219.117111    -828.362610
2018-03-11 10:00:00.020     219.414963    -828.970520
2018-03-11 10:00:00.040     219.210724    -828.194641
2018-03-11 10:00:00.060     218.844788    -828.614563
2018-03-11 10:00:00.080     218.921371    -827.882690
2018-03-11 10:00:00.100     218.129944    -827.966675
2018-03-11 10:00:00.120     218.942657    -828.466614
2018-03-11 10:00:00.140     218.972443    -827.926636
2018-03-11 10:00:00.160     218.712875    -828.346619
2018-03-11 10:00:00.180     219.397934    -828.506592
...                                ...            ...
2018-03-11 10:00:04.800     219.414963    -827.398743
2018-03-11 10:00:04.820     219.274536    -827.738708
2018-03-11 10:00:04.840     220.389359    -827.078796
2018-03-11 10:00:04.860     219.602173    -827.606689
2018-03-11 10:00:04.880     218.891586    -827.230774
2018-03-11 10:00:04.900     219.036255    -828.046631
2018-03-11 10:00:04.920     218.989456    -828.566589
2018-03-11 10:00:04.940     219.036255    -828.790527
2018-03-11 10:00:04.960     218.619263    -829.030518
2018-03-11 10:00:04.980     218.891586    -828.614563

[250 rows x 2 columns]

In [59]:
df3

NLHQ-X-03-S08  NLHQ-X-03-S09
2018-03-11 10:00:05.000     219.414963    -828.202637
2018-03-11 10:00:05.020     218.844788    -828.134644
2018-03-11 10:00:05.040     220.172348    -827.182739
2018-03-11 10:00:05.060     219.512817    -827.010803
2018-03-11 10:00:05.080     219.648987    -827.882690
2018-03-11 10:00:05.100     219.759613    -828.258606
2018-03-11 10:00:05.120     219.180939    -829.014526
2018-03-11 10:00:05.140     219.066040    -829.358459
2018-03-11 10:00:05.160     218.376740    -829.222473
2018-03-11 10:00:05.180     218.495880    -829.298462
...                                ...            ...
2018-03-11 10:00:09.800     219.427719    -827.530701
2018-03-11 10:00:09.820     219.959595    -828.314636
2018-03-11 10:00:09.840     218.670334    -828.894531
2018-03-11 10:00:09.860     218.797974    -829.954407
2018-03-11 10:00:09.880     218.908615    -829.298462
2018-03-11 10:00:09.900     218.942657    -828.762573
2018-03-11 10:00:09.920     218.768188    -828.050659
2018-03-11 10:00:09.940     219.589417    -827.886658
2018-03-11 10:00:09.960     219.461761    -827.214722
2018-03-11 10:00:09.980     219.491547    -827.386719

[250 rows x 2 columns]

In [60]:
# 定义Pandas DataFrame重组的函数
def convert_df(df):
    index = pd.MultiIndex.from_product([[df.index[0]], df.index], names=['start_time', 'timestamp'])
    df = pd.DataFrame(data=df.values, index=index, columns=df.columns)
    return df

## 组合为多重索引数据包
* 第一层索引为数据包的起始时间
* 第二层索引为每个数据点对应的时间

**注意：**再组合的过程中已对数据包进行升序排列

In [61]:
df1 = convert_df(df1)
df2 = convert_df(df2)
df3 = convert_df(df3)

df4 = df1.combine_first(df2).combine_first(df3)
df4

NLHQ-X-03-S08  NLHQ-X-03-S09
start_time          timestamp                                            
2018-03-11 10:00:00 2018-03-11 10:00:00.000     219.117111    -828.362610
                    2018-03-11 10:00:00.020     219.414963    -828.970520
                    2018-03-11 10:00:00.040     219.210724    -828.194641
                    2018-03-11 10:00:00.060     218.844788    -828.614563
                    2018-03-11 10:00:00.080     218.921371    -827.882690
                    2018-03-11 10:00:00.100     218.129944    -827.966675
                    2018-03-11 10:00:00.120     218.942657    -828.466614
                    2018-03-11 10:00:00.140     218.972443    -827.926636
                    2018-03-11 10:00:00.160     218.712875    -828.346619
                    2018-03-11 10:00:00.180     219.397934    -828.506592
...                                                    ...            ...
2018-03-11 10:00:10 2018-03-11 10:00:14.800     218.780960    -828.986511
                    2018-03-11 10:00:14.820     217.853363    -831.098267
                    2018-03-11 10:00:14.840     217.823578    -830.822266
                    2018-03-11 10:00:14.860     218.780960    -829.834412
                    2018-03-11 10:00:14.880     219.083069    -828.018616
                    2018-03-11 10:00:14.900     219.572388    -826.294861
                    2018-03-11 10:00:14.920     220.419144    -826.074890
                    2018-03-11 10:00:14.940     220.461700    -826.234863
                    2018-03-11 10:00:14.960     219.648987    -826.346863
                    2018-03-11 10:00:14.980     220.525528    -826.898804

[750 rows x 2 columns]

### 获取第一层索引值的无重复列表

In [62]:
start_time_index = df4.index.get_level_values(level='start_time')
unique_values = start_time_index.unique()
unique_values.format()

['2018-03-11 10:00:00', '2018-03-11 10:00:05', '2018-03-11 10:00:10']

### 通过第一层索引值无重复列表的各个项可获得原始数据包

In [63]:
df4.loc[unique_values[0]]

NLHQ-X-03-S08  NLHQ-X-03-S09
timestamp                                            
2018-03-11 10:00:00.000     219.117111    -828.362610
2018-03-11 10:00:00.020     219.414963    -828.970520
2018-03-11 10:00:00.040     219.210724    -828.194641
2018-03-11 10:00:00.060     218.844788    -828.614563
2018-03-11 10:00:00.080     218.921371    -827.882690
2018-03-11 10:00:00.100     218.129944    -827.966675
2018-03-11 10:00:00.120     218.942657    -828.466614
2018-03-11 10:00:00.140     218.972443    -827.926636
2018-03-11 10:00:00.160     218.712875    -828.346619
2018-03-11 10:00:00.180     219.397934    -828.506592
...                                ...            ...
2018-03-11 10:00:04.800     219.414963    -827.398743
2018-03-11 10:00:04.820     219.274536    -827.738708
2018-03-11 10:00:04.840     220.389359    -827.078796
2018-03-11 10:00:04.860     219.602173    -827.606689
2018-03-11 10:00:04.880     218.891586    -827.230774
2018-03-11 10:00:04.900     219.036255    -828.046631
2018-03-11 10:00:04.920     218.989456    -828.566589
2018-03-11 10:00:04.940     219.036255    -828.790527
2018-03-11 10:00:04.960     218.619263    -829.030518
2018-03-11 10:00:04.980     218.891586    -828.614563

[250 rows x 2 columns]

### 从第一个数据包减除所有数据包的众数

In [64]:
df4.loc[unique_values[0]]-df4.mode().loc[0].values

NLHQ-X-03-S08  NLHQ-X-03-S09
timestamp                                            
2018-03-11 10:00:00.000       0.127655      -1.099854
2018-03-11 10:00:00.020       0.425507      -1.707764
2018-03-11 10:00:00.040       0.221268      -0.931885
2018-03-11 10:00:00.060      -0.144669      -1.351807
2018-03-11 10:00:00.080      -0.068085      -0.619934
2018-03-11 10:00:00.100      -0.859512      -0.703918
2018-03-11 10:00:00.120      -0.046799      -1.203857
2018-03-11 10:00:00.140      -0.017014      -0.663879
2018-03-11 10:00:00.160      -0.276581      -1.083862
2018-03-11 10:00:00.180       0.408478      -1.243835
...                                ...            ...
2018-03-11 10:00:04.800       0.425507      -0.135986
2018-03-11 10:00:04.820       0.285080      -0.475952
2018-03-11 10:00:04.840       1.399902       0.183960
2018-03-11 10:00:04.860       0.612717      -0.343933
2018-03-11 10:00:04.880      -0.097870       0.031982
2018-03-11 10:00:04.900       0.046799      -0.783875
2018-03-11 10:00:04.920       0.000000      -1.303833
2018-03-11 10:00:04.940       0.046799      -1.527771
2018-03-11 10:00:04.960      -0.370193      -1.767761
2018-03-11 10:00:04.980      -0.097870      -1.351807

[250 rows x 2 columns]

### 从组合数据包中删除第一个数据包

In [65]:
df4.drop(index=unique_values[0], level='start_time')

NLHQ-X-03-S08  NLHQ-X-03-S09
start_time          timestamp                                            
2018-03-11 10:00:05 2018-03-11 10:00:05.000     219.414963    -828.202637
                    2018-03-11 10:00:05.020     218.844788    -828.134644
                    2018-03-11 10:00:05.040     220.172348    -827.182739
                    2018-03-11 10:00:05.060     219.512817    -827.010803
                    2018-03-11 10:00:05.080     219.648987    -827.882690
                    2018-03-11 10:00:05.100     219.759613    -828.258606
                    2018-03-11 10:00:05.120     219.180939    -829.014526
                    2018-03-11 10:00:05.140     219.066040    -829.358459
                    2018-03-11 10:00:05.160     218.376740    -829.222473
                    2018-03-11 10:00:05.180     218.495880    -829.298462
...                                                    ...            ...
2018-03-11 10:00:10 2018-03-11 10:00:14.800     218.780960    -828.986511
                    2018-03-11 10:00:14.820     217.853363    -831.098267
                    2018-03-11 10:00:14.840     217.823578    -830.822266
                    2018-03-11 10:00:14.860     218.780960    -829.834412
                    2018-03-11 10:00:14.880     219.083069    -828.018616
                    2018-03-11 10:00:14.900     219.572388    -826.294861
                    2018-03-11 10:00:14.920     220.419144    -826.074890
                    2018-03-11 10:00:14.940     220.461700    -826.234863
                    2018-03-11 10:00:14.960     219.648987    -826.346863
                    2018-03-11 10:00:14.980     220.525528    -826.898804

[500 rows x 2 columns]

### 从索引值无重复列表中删除一个元素

In [66]:
unique_values.delete(0).format()

['2018-03-11 10:00:05', '2018-03-11 10:00:10']